### Importing Libraries and Constants Definition

In [1]:
!pip install pandas numpy scikit-learn transformers torch

import pandas as pd
import numpy as np
import logging
from sklearn.metrics.pairwise import cosine_similarity
from transformers import BertTokenizer, BertModel
import torch

logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

DATA_PATH = '../data/public/'
PROPOSALS_FILE = DATA_PATH + 'brasilparticipativo.presidencia.gov.br-open-data-proposals.csv'
VOCAB_FILE = DATA_PATH + 'vocabulario-controlado-basico-vcb-lista-alfabetica.txt'
TOP_N_TOPICS = 5

### Set up GPU

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

### Load BERT model and tokenizer

In [ ]:
tokenizer = BertTokenizer.from_pretrained("neuralmind/bert-base-portuguese-cased")
model = BertModel.from_pretrained("neuralmind/bert-base-portuguese-cased").to(device)

Some weights of the model checkpoint at neuralmind/bert-base-portuguese-cased were not used when initializing BertModel: ['cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


### Functions Definition

In [ ]:
def process_vocab_file(vocab_file):
    ROWS_TO_SKIP = 8
    vocab_dict = {}
    with open(vocab_file, 'r', encoding='utf-8') as file:
        current_term = ''
        for line in file.read().splitlines()[ROWS_TO_SKIP:]:
            if not line.startswith('\t') and line != '':
                current_term = line
                vocab_dict[current_term] = {
                    'USE': [], # Use
                    'DF': [],  # Definição
                    'UP': [],  # Termos não preferenciais
                    'TG': [],  # Termo geral
                    'TR': [],  # Termos relacionados
                    'TE': [],  # Termos específicos
                    'EQ': [],  # Equivalente
                    'Nota de escopo': [],
                }
            elif line != '':
                property = line.strip().split(':')
                key = property[0].strip()
                value = property[1].strip()
                vocab_dict[current_term][key].append(value)
    return vocab_dict

def process_vocab(vocab_file, exclusion_terms):
    vocab_json = process_vocab_file(vocab_file)
    vocab_list_processed = [key for key in vocab_json if key.lower() not in exclusion_terms]
    return vocab_list_processed

def load_and_preprocess_proposals(file_path):
    df = pd.read_csv(file_path, delimiter=';')
    # df = df[~df['state'].isin(['rejected', 'withdrawn'])]
    df['body/pt-BR'] = df['body/pt-BR'].str.replace(r'<[^>]*>', '', regex=True)
    relevant_cols = [
        'id',
        'category/id',
        'category/name/pt-BR',
        'title/pt-BR',
        'body/pt-BR',
        'supports',
        'followers',
        'comments',
        'published_at',
        'state', # REMOVE
        'url',
        'participatory_space/url',
    ]
    return df[relevant_cols]

def get_unique_themes(df):
    themes = df['category/name/pt-BR'].str.lower().unique().tolist()
    themes = [str(theme) for theme in themes if theme is not np.nan]
    themes = set([theme.split('- direito à')[-1].strip() for theme in themes])
    themes = set([theme.split('- direito ao')[-1].strip() for theme in themes])
    return themes


def get_embedding(sentence):
    print(sentence)
    tokens = tokenizer.tokenize(sentence)
    tokens = ['[CLS]'] + tokens + ['[SEP]']
    input_ids = tokenizer.convert_tokens_to_ids(tokens)
    input_ids = torch.tensor([input_ids]).to(device)

    with torch.no_grad():
        output = model(input_ids)
        embeddings = output.last_hidden_state.mean(dim=1)
    return embeddings

def classify_topics(sentences, topics, top_n=TOP_N_TOPICS):
    # Convert sentences and topics to BERT embeddings
    print("sentence_embeddings = [get_embedding(sentence) for sentence in sentences]")
    sentence_embeddings = [get_embedding(sentence) for sentence in sentences]
    print("topic_embeddings = [get_embedding(topic) for topic in topics]")
    topic_embeddings = [get_embedding(topic) for topic in topics]

    classified_data = []

    for i, sentence_embedding in enumerate(sentence_embeddings):
        print(i, len(sentence_embeddings))
        cosine_similarities = cosine_similarity(sentence_embedding.cpu().numpy(), np.array([t.cpu().numpy() for t in topic_embeddings]).squeeze(1))
        top_n_indices = np.argsort(cosine_similarities[0])[-top_n:][::-1]
        top_n_topic_similarities = [(topics[idx], cosine_similarities[0][idx]) for idx in top_n_indices]
        classified_data.append((sentences[i], top_n_topic_similarities))

    return classified_data

### Loading and preprocessing proposals

In [ ]:
df_propostas = load_and_preprocess_proposals(PROPOSALS_FILE)
df_propostas.head(5)

id  category/id                             category/name/pt-BR  \
0   1         30.0                                         Turismo   
1   8         31.0  Desenvolvimento Agrário e Agricultura Familiar   
2   9          1.0                          Agricultura e Pecuária   
3  10         27.0                                           Saúde   
4  11         27.0                                           Saúde   

                           title/pt-BR  \
0            Turismo: esse é o Destino   
1  Agricultura Familiar e Agroecologia   
2             Agropecuária Sustentável   
3             Atenção Primária à Saúde   
4        Atenção Especializada à Saúde   

                                          body/pt-BR  supports  followers  \
0  Objetivo: Posicionar o turismo como vetor de d...         1          1   
1  Objetivo: Fortalecer a agricultura familiar em...         1          0   
2  Objetivo: Contribuir para o desenvolvimento do...         2          0   
3  Fortalecer a Atenção Primária à Saúde, amplian...     20427        515   
4  Ampliar o acesso às ações e serviços da Atençã...     18786        383   

   comments               published_at state  \
0         0  2023-05-10 10:03:41 -0300   NaN   
1         0  2023-05-10 16:22:51 -0300   NaN   
2         0  2023-05-10 16:35:47 -0300   NaN   
3         0  2023-05-10 16:42:43 -0300   NaN   
4         0  2023-05-10 16:41:01 -0300   NaN   

                                                 url  \
0  http://brasilparticipativo.presidencia.gov.br/...   
1  http://brasilparticipativo.presidencia.gov.br/...   
2  http://brasilparticipativo.presidencia.gov.br/...   
3  http://brasilparticipativo.presidencia.gov.br/...   
4  http://brasilparticipativo.presidencia.gov.br/...   

                             participatory_space/url  
0  http://brasilparticipativo.presidencia.gov.br/...  
1  http://brasilparticipativo.presidencia.gov.br/...  
2  http://brasilparticipativo.presidencia.gov.br/...  
3  http://brasilparticipativo.presidencia.gov.br/...  
4  http://brasilparticipativo.presidencia.gov.br/...

### Extracting sentences from proposals and titles

In [ ]:
df_propostas['sentence'] = df_propostas['title/pt-BR'].str.lower() + ' ' + df_propostas['body/pt-BR'].str.lower()
sentences = df_propostas['sentence'].tolist()
sentences[:5]

['turismo: esse é o destino objetivo: posicionar o turismo como vetor de desenvolvimento sustentável e aumentar a competitividade dos destinos e produtos turísticos brasileiros, democratizando o acesso à atividade turística aos cidadãos brasileiros.órgão responsável: ministério do turismopágina oficial: https://www.gov.br/turismo/pt-br/',
 'agricultura familiar e agroecologia objetivo: fortalecer a agricultura familiar em sua diversidade e a agroecologia, promovendo a inclusão socioeconômica, com fomento à produção sustentável e à geração de renda, contribuindo para a promoção da segurança alimentar e nutricional e da vida digna, com redução das desigualdades e mitigação das mudanças climáticas.órgão responsável: ministério do desenvolvimento agráriopágina oficial: https://www.gov.br/agricultura/pt-br/assuntos/mda/agricultura-familiar-1',
 'agropecuária sustentável objetivo: contribuir para o desenvolvimento do setor agropecuário, com sustentabilidade ambiental, econômica e social, por

### Getting unique themes

In [ ]:
themes = get_unique_themes(df_propostas)
list(themes)[:5]

['secretaria geral da presidência da república',
 'planejamento e orçamento',
 'desenvolvimento agrário e agricultura familiar',
 'igualdade racial',
 'outros']

### Processing vocabulary

In [ ]:
vocab_list = process_vocab(VOCAB_FILE, themes)
vocab_list[:10]

['2019-nCoV disease',
 '2FA',
 '2Factor Authentication',
 'AAE',
 'Ab-rogação',
 'Abacate',
 'Abacaxi',
 'Abalo sísmico',
 'Abalroamento aéreo',
 'Abalroamento de navios']

### Classifying topics

In [ ]:
classified_topics = classify_topics(sentences, vocab_list)
classified_topics[:3]

sentence_embeddings = [get_embedding(sentence) for sentence in sentences]
turismo: esse é o destino objetivo: posicionar o turismo como vetor de desenvolvimento sustentável e aumentar a competitividade dos destinos e produtos turísticos brasileiros, democratizando o acesso à atividade turística aos cidadãos brasileiros.órgão responsável: ministério do turismopágina oficial: https://www.gov.br/turismo/pt-br/
agricultura familiar e agroecologia objetivo: fortalecer a agricultura familiar em sua diversidade e a agroecologia, promovendo a inclusão socioeconômica, com fomento à produção sustentável e à geração de renda, contribuindo para a promoção da segurança alimentar e nutricional e da vida digna, com redução das desigualdades e mitigação das mudanças climáticas.órgão responsável: ministério do desenvolvimento agráriopágina oficial: https://www.gov.br/agricultura/pt-br/assuntos/mda/agricultura-familiar-1
agropecuária sustentável objetivo: contribuir para o desenvolvimento do setor agrop

### Processing classified topics

In [ ]:
classified_topics_processed = [[sentence] + [f"{x[0]} ({round(x[1]*100)}%)" for x in topics] for sentence, topics in classified_topics]
classified_topics_processed[:3]

### Creating DataFrame with classified topics

In [ ]:
columns = ['sentence'] + [f"Tópico {i}" for i in range(1, TOP_N_TOPICS + 1)]
df_classified = pd.DataFrame(classified_topics_processed, columns=columns)
df_classified.head(5)

### Merging dataframes

In [ ]:
df_merged = pd.merge(df_propostas, df_classified, on='sentence', how='left')
df_merged.head(5)

### Identifying Participative Processes

In [ ]:
conjuv_url = df_merged['participatory_space/url'].tolist()[-1]
conjuv = conjuv_url.split('/')[3] + '|' + conjuv_url.split('/')[4].split('?')[0]  + '|' + conjuv_url.split('=')[-1]
program_url = df_merged['participatory_space/url'].tolist()[0]
program = program_url.split('/')[3] + '|' + program_url.split('/')[4].split('?')[0]  + '|' + program_url.split('=')[-1]
set(df_merged['participatory_space/url'].tolist()), conjuv, program

In [ ]:
df_merged['participatory_space'] = df_merged['participatory_space/url'].str.split('/').str[3] + '|' + \
                                  df_merged['participatory_space/url'].str.split('/').str[4].str.split('?').str[0] + '|' + \
                                  df_merged['participatory_space/url'].str.split('/').str[4].str.split('=').str[-1]
df_merged['participatory_space']

### Renaming columns

In [ ]:
df_merged_renamed = df_merged[['id', 'state', 'participatory_space', 'category/name/pt-BR', 'supports', 'title/pt-BR', 'body/pt-BR', 'Tópico 1', 'Tópico 2', 'Tópico 3', 'Tópico 4', 'Tópico 5']] \
    .rename(columns={
        'id': 'id_proposta',
        'state': 'status',
        'participatory_space': 'programa',
        'category/name/pt-BR': 'tema',
        'supports': 'votos',
        'title/pt-BR': 'titulo',
        'body/pt-BR': 'proposta'
    })
df_merged_renamed

### Saving to file

In [ ]:
OUTPUT_FILE = DATA_PATH + 'results_TopicClassification_BERT_CosineSimilarity.csv'
df_merged = df_merged.drop_duplicates()
df_merged.to_csv(OUTPUT_FILE, index=False)